In [1]:
from sklearn.preprocessing import StandardScaler
from model_trees_algebra import NeoRegression
from sklearn.metrics import mean_squared_error, mean_absolute_error
import numpy as np
import pandas as pd
import torch.nn as nn

URL = "/workspace/TreeConvolution/DS_WIKIDATA_TESIS/"

class BaoTrainingException(Exception):
    pass

from sklearn.model_selection import train_test_split
def split_ds(all_data, val_rate, seed):
    """test_rate is a rate of the total, val_rate is a rate of the (total - test_rate)"""
    ranges = {}
    ranges['1_2'] = all_data[(all_data["time"] > 0)    & (all_data["time"] <= 2)]
    ranges['2_3'] = all_data[(all_data["time"] > 2)    & (all_data["time"] <= 3)]
    ranges['3_4'] = all_data[(all_data["time"] > 3)    & (all_data["time"] <= 4)]
    ranges['4_5'] = all_data[(all_data["time"] > 4)    & (all_data["time"] <= 5)]
    ranges['5_8'] = all_data[(all_data["time"] > 5)    & (all_data["time"] <= 8)]
    ranges['8_10'] = all_data[(all_data["time"] > 8)   & (all_data["time"] <= 10)]
    ranges['10_20'] =   all_data[(all_data["time"] > 10) & (all_data["time"] <= 20)]
    ranges['20_30'] =   all_data[(all_data["time"] > 20) & (all_data["time"] <= 30)]
    ranges['30_40'] =   all_data[(all_data["time"] > 30) & (all_data["time"] <= 40)]
    ranges['40_50'] =   all_data[(all_data["time"] > 40) & (all_data["time"] <= 50)]
    ranges['50_60'] =   all_data[(all_data["time"] > 50) & (all_data["time"] <= 60)]
    ranges['60_80'] =   all_data[(all_data["time"] > 60) & (all_data["time"] <= 80)]
    ranges['80_100'] =  all_data[(all_data["time"] > 80) & (all_data["time"] <= 100)]
    ranges['100_150'] = all_data[(all_data["time"] > 100) & (all_data["time"] <= 150)]
    ranges['150_200'] = all_data[(all_data["time"] > 150) & (all_data["time"] <= 200)]
    ranges['200_250'] = all_data[(all_data["time"] > 200) & (all_data["time"] <= 250)]
    ranges['250_last'] = all_data[(all_data["time"] > 250)]
    train_data = []
    val_data = []
    test_data = []
    for rang in ranges.values():
        if rang.shape[0] >= 3:
            X_train, X_val = train_test_split(
                rang, test_size=val_rate, shuffle=True,random_state=seed)

            train_data.append(X_train)
            val_data.append(X_val)
    train_data_list = pd.concat(train_data)
    val_data_list = pd.concat(val_data)
    print("Shapes : Train: {} Val: {}".format(train_data_list.shape, val_data_list.shape))
    return train_data_list, val_data_list

# ds_test = pd.read_csv(URL + "ds_test_pred_filtered.csv", delimiter="ᶶ", engine='python')
data_train_val = pd.read_csv(URL + "ds_trainval_pred_filtered.csv", delimiter="ᶶ", engine='python')

data_train_val = data_train_val[data_train_val['time'] <=65]
# ds_test = ds_test[ds_test['time'] <=65]

print("Shape: train_val data" , data_train_val.shape)
import json
def clear_error_tuples(x):
    try:
        x_tree = json.loads(x)
        return True
    except:
        print("Error in data ignored!", x)
        return False

#Datasets
datasets_splits = []
for fold in range(5):
    # We use a fold bar as seed for reproductibility
    ds_train, ds_val = split_ds(data_train_val, 0.5, seed=fold)
    ds_train  = ds_train[ds_train['trees'].apply(lambda x: clear_error_tuples(x))]
    ds_val  = ds_val[ds_val['trees'].apply(lambda x: clear_error_tuples(x))]

    datasets_splits.append({"train": ds_train, "val" :ds_val})


IS CUDA AVAILABLE: True
IS CUDA AVAILABLE: True
IS CUDA AVAILABLE: True
IS CUDA AVAILABLE: True
Shape: train_val data (21703, 84)
Shapes : Train: (10850, 84) Val: (10853, 84)
Error in data ignored! [bgp "VAR_URI_VARᶲhttp://www.wikidata.org/prop/direct/P685"]
Error in data ignored! [reduced   ["VAR_VAR_VARᶲNONE"]]
Error in data ignored! [datasetnames ?var1]
Error in data ignored! [reduced   ["VAR_VAR_VARᶲNONE"]]
Error in data ignored! [reduced   ["VAR_VAR_VARᶲNONE"]]
Error in data ignored! [reduced   ["VAR_VAR_VARᶲNONE"]]
Shapes : Train: (10850, 84) Val: (10853, 84)
Error in data ignored! [datasetnames ?var1]
Error in data ignored! [reduced   ["VAR_VAR_VARᶲNONE"]]
Error in data ignored! [reduced   ["VAR_VAR_VARᶲNONE"]]
Error in data ignored! [reduced   ["VAR_VAR_VARᶲNONE"]]
Error in data ignored! [reduced   ["VAR_VAR_VARᶲNONE"]]
Error in data ignored! [bgp "VAR_URI_VARᶲhttp://www.wikidata.org/prop/direct/P685"]
Shapes : Train: (10850, 84) Val: (10853, 84)
Error in data ignored! [dataset

In [20]:
for fold, data in enumerate(datasets_splits):
    data['train'].to_pickle("./fold_data_"+str(fold)+"_train.pickle")
    data['val'].to_pickle("./fold_data_"+str(fold)+"_val.pickle")
# file_to_store = open("./folds_execution_baseline.pickle", "wb")
# pickle.dump(folds_execution, file_to_store)
# file_to_store.close()

In [16]:
from torch.utils.data import DataLoader
import json

def getpredictions_info(x_val_tree, x_val_query, y_val):
    Xt, Xq, Yv = reg.json_loads(x_val_tree, x_val_query.values, y_val)
    Xt = [reg.fix_tree(x) for x in Xt]
    Xt = reg.tree_transform.transform(Xt)

    pairs_val = list(zip(list(zip(Xt, Xq)), Yv))
    dataset_val = DataLoader(pairs_val, batch_size=64, num_workers=0, shuffle=False, collate_fn=reg.collate_with_card)
    results_val = reg.predict_best(dataset_val)
    y_pred_val, y_real_val = zip(*results_val)
    mseval = mean_squared_error(y_real_val, y_pred_val)
    maeval = mean_absolute_error(y_real_val, y_pred_val)
    rmseval = np.sqrt(mseval)
    return {"pred": y_pred_val, "real" : y_real_val, "mse": mseval, "mae": maeval, "rmse": rmseval, "history": reg.history}

def getmax(x):
    lista=  list(x.values())
    maximo = 0
    for el in lista:
        if (maximo < float(el)):
            maximo = float(el)
    return maximo

def getpreds(values, preds_dic):
    index = len(preds_dic)
    for x in values:
        lista=  list(json.loads(x).keys())
        for el in lista:
            if not el.startswith("http"):
                continue
            if el not in preds_dic:
                preds_dic[el] = index
                index +=1
    return preds_dic

def pred2index_dict(x, pred_to_index, maxcardinality):
    resp = {}
    x = json.loads(x)
    for el in x.keys():
        if el in pred_to_index:
            resp[pred_to_index[el]] = float(x[el])/maxcardinality
    return resp

def prepare_query_level_data(x_train_query, x_val_query):
    """ Apply StandardScaller to columns except for json_cardinality that need other proccess"""
    maxcardinality =  x_train_query['json_cardinality'].apply(lambda x: json.loads(x)).apply(lambda x: getmax(x)).max()
    #Scale x_query data.
    xqtrain = x_train_query.drop(columns=['json_cardinality'])
    xqval   = x_val_query.drop(columns=['json_cardinality'])

    scalerx = StandardScaler()
    x_train_scaled = scalerx.fit_transform(xqtrain)
    x_val_scaled = scalerx.transform(xqval)

    x_train_query =pd.concat([pd.DataFrame(x_train_scaled, index=xqtrain.index, columns=xqtrain.columns),x_train_query[['json_cardinality']]], axis=1)
    x_val_query =  pd.concat([pd.DataFrame(x_val_scaled,   index=xqval.index, columns=xqval.columns),x_val_query[['json_cardinality']]], axis=1)

    x_train_query['json_cardinality'] = x_train_query['json_cardinality'].apply(lambda x: pred2index_dict(x, reg.get_pred(),maxcardinality))
    x_val_query['json_cardinality'] = x_val_query['json_cardinality'].apply(lambda x: pred2index_dict(x, reg.get_pred(), maxcardinality))
    
    return x_train_query, x_val_query


In [8]:
# def run_baseline(x_train_query, y_train, x_val_query, y_val):
#     #Scale x_query data.
#     xqtrain = x_train_query.drop(columns=['json_cardinality'])
#     xqval   = x_val_query.drop(columns=['json_cardinality'])

#     scalerx = StandardScaler()
#     x_train_scaled = scalerx.fit_transform(xqtrain)
#     x_val_scaled = scalerx.transform(xqval)

#     x_train_query =pd.concat([pd.DataFrame(x_train_scaled, index=xqtrain.index, columns=xqtrain.columns),x_train_query[['json_cardinality']]], axis=1)
#     x_val_query =  pd.concat([pd.DataFrame(x_val_scaled,   index=xqval.index, columns=xqval.columns),x_val_query[['json_cardinality']]], axis=1)

#     preds_dic = {"other": 0}
#     preds_dic = getpreds(x_train_query['json_cardinality'], preds_dic)
#     preds_dic = getpreds(x_val_query['json_cardinality'], preds_dic)

#     maxcardinality =  x_train_query['json_cardinality'].apply(lambda x: json.loads(x)).apply(lambda x: getmax(x)).max()

#     def pred2index_dict(x, pred_to_index):
#         resp = {}
#         x = json.loads(x)
#         for el in x.keys():
#             if el in pred_to_index:
#                 resp[pred_to_index[el]] = float(x[el])/maxcardinality
#         return resp

#     x_train_query['json_cardinality'] = x_train_query['json_cardinality'].apply(lambda x: pred2index_dict(x, preds_dic))
#     x_val_query['json_cardinality'] = x_val_query['json_cardinality'].apply(lambda x: pred2index_dict(x, preds_dic))
#     y_train = ds_train['time'].values
#     y_val = ds_val['time'].values
#     return run_baseline(x_train_query.values, y_train, x_val_query.values, y_val, maxcardinality,  preds_dic)

### Hipotesis Test 5x2cv

### P1(TreeConv Neural Net)

In [ ]:
list_columns = ['assign', 'bgp', 'distinct', 'extend', 'filter', 'graph', 'group',
'join', 'leftjoin','minus', 'multi', 'notoneof', 'order', 'path*',  'project', 'reduced',
'sequence', 'slice', 'tolist', 'top','treesize', 'triple', 'union' ,
'path+', 'path?', 'pathN*', 'pathN+', 'pcs0', 'pcs1', 'pcs2', 'pcs3', 'pcs4',
'pcs5', 'pcs6', 'pcs7', 'pcs8', 'pcs9', 'pcs10', 'pcs11','pcs12', 'pcs13',
'pcs14', 'pcs15', 'pcs16', 'pcs17', 'pcs18', 'pcs19', 'pcs20', 'pcs21', 'pcs22', 'pcs23', 'pcs24',
                'filter_bound', 'filter_contains', 'filter_eq', 'filter_exists',
       'filter_ge', 'filter_gt', 'filter_isBlank', 'filter_isIRI',
       'filter_isLiteral', 'filter_lang', 'filter_langMatches', 'filter_le',
       'filter_lt', 'filter_ne', 'filter_not', 'filter_notexists', 'filter_or',
       'filter_regex', 'filter_sameTerm', 'filter_str', 'filter_strends',
       'filter_strstarts', 'filter_subtract', 'has_slice', 'max_slice_limit', 'max_slice_start','json_cardinality']
import pickle
folds_execution = {}

for fold, data in enumerate(datasets_splits):
    
    ds_train = data['train']
    ds_val = data['val']
    print("Size Train: {}, Val {}, Fold".format(ds_train.shape[0], ds_val.shape[0]), fold)
    
    x_train_query = ds_train[list_columns]
    x_val_query   = ds_val[list_columns]

    x_train_tree = ds_train['trees'].values
    x_val_tree = ds_val['trees'].values

    y_train = ds_train['time'].values
    y_val = ds_val['time'].values



    x_train_tree = ds_train['trees'].values
    x_val_tree = ds_val['trees'].values

    y_train = ds_train['time'].values
    y_val = ds_val['time'].values

    aec_dir = '/workspace/bao_server/aec_wikidata_neo.pth'
    maxcardinality =  x_train_query['json_cardinality'].apply(lambda x: json.loads(x)).apply(lambda x: getmax(x)).max()

    verbose=True
    reg = NeoRegression(
         aec={'train_aec': False, 'use_aec': True,'aec_file': aec_dir+str(fold)+'.pth', 'aec_epochs': 200},
         epochs=300,
         maxcardinality=maxcardinality,
         in_channels_neo_net=512,
         tree_units=[512, 256, 128],
         tree_units_dense=[64, 32],
         early_stop_patience=10,
         early_stop_initial_patience=180,
         tree_activation_tree=nn.LeakyReLU,
         tree_activation_dense=nn.ReLU,
        optimizer={'optimizer': "Adam",'args':{"lr":0.00015}},
        figimage_size=(18,18),
        start_history_from_epoch=3
    )

    #Fit the transformer tree data
    reg.fit_transform_tree_data(ds_train, ds_val, ds_val)
    print("Trees tranformed!!!")

    x_train_query, x_val_query =  prepare_query_level_data(x_train_query, x_val_query)

    #Fit model
    reg.fit(x_train_tree, x_train_query.values, y_train, x_val_tree, x_val_query.values, y_val)
    folds_execution[fold] = {"tree_model": getpredictions_info(x_val_tree, x_val_query, y_val)}

file_to_store = open("./folds_execution.pickle", "wb")
pickle.dump(folds_execution, file_to_store)
file_to_store.close()
#     run_baseline(x_train_query, y_train, x_val_query, y_val)
#     folds_execution[fold] = {"tree_model": getpreds(x_val_tree, x_val_query, y_val)}

Size Train: 10850, Val 10853, Fold 0
Model optimizer: Adam lr: 0.00015
Error in data ignored! [bgp "VAR_URI_VARᶲhttp://www.wikidata.org/prop/direct/P685"]
Error in data ignored! [reduced   ["VAR_VAR_VARᶲNONE"]]
Error in data ignored! [datasetnames ?var1]
Error in data ignored! [reduced   ["VAR_VAR_VARᶲNONE"]]
Error in data ignored! [reduced   ["VAR_VAR_VARᶲNONE"]]
Error in data ignored! [reduced   ["VAR_VAR_VARᶲNONE"]]
Error in data ignored! [datasetnames ?var1]
Error in data ignored! [reduced   ["VAR_VAR_VARᶲNONE"]]
Error in data ignored! [reduced   ["VAR_VAR_VARᶲNONE"]]
Error in data ignored! [reduced   ["VAR_VAR_VARᶲNONE"]]
Trees tranformed!!!
Error in data ignored! ('[bgp "VAR_URI_VARᶲhttp://www.wikidata.org/prop/direct/P685"]', array([0.0, -0.264113788729782, -0.9941186771667332, -0.3707414548887624,
       -0.7590541261977151, 0.0, -0.44046431789137874,
       -0.22141582907959934, -0.3894622358234045, 0.0, 0.0,
       -0.29011181998932284, -0.1726342423301504, -0.185446336439559

[2021-01-13 04:43:52,035] INFO:model_trees_algebra:==> Epoch 0,	TRAIN_LOSS: 2086.5621302382683	_TRAIN_RMSE: 45.67890246315325,	VAL_LOSS: 6036.669801370691,	VAL_RMSE: 77.69600891532777


Initial patience 180
2021-01-13 04:44:05.945951 Epoch 1, Training loss 0.00021315404043168758


[2021-01-13 04:44:15,813] INFO:model_trees_algebra:==> Epoch 1,	TRAIN_LOSS: 16068.253188944811	_TRAIN_RMSE: 126.76061371319093,	VAL_LOSS: 359.4679446878325,	VAL_RMSE: 18.95963988813692


Initial patience 179
2021-01-13 04:44:35.047039 Epoch 2, Training loss 0.00014207684503429952


...

Initial patience 168
2021-01-13 11:10:12.340964 Epoch 13, Training loss 5.543947311691863e-05


[2021-01-13 11:10:22,574] INFO:model_trees_algebra:==> Epoch 13,	TRAIN_LOSS: 28.01937738937503	_TRAIN_RMSE: 5.293333296645416,	VAL_LOSS: 42.67178583705789,	VAL_RMSE: 6.532364490523924
[2021-01-13 11:10:22,574] INFO:model_trees_algebra:==> Epoch 13,	TRAIN_LOSS: 28.01937738937503	_TRAIN_RMSE: 5.293333296645416,	VAL_LOSS: 42.67178583705789,	VAL_RMSE: 6.532364490523924
[2021-01-13 11:10:22,574] INFO:model_trees_algebra:==> Epoch 13,	TRAIN_LOSS: 28.01937738937503	_TRAIN_RMSE: 5.293333296645416,	VAL_LOSS: 42.67178583705789,	VAL_RMSE: 6.532364490523924
[2021-01-13 11:10:22,574] INFO:model_trees_algebra:==> Epoch 13,	TRAIN_LOSS: 28.01937738937503	_TRAIN_RMSE: 5.293333296645416,	VAL_LOSS: 42.67178583705789,	VAL_RMSE: 6.532364490523924
[2021-01-13 11:10:22,574] INFO:model_trees_algebra:==> Epoch 13,	TRAIN_LOSS: 28.01937738937503	_TRAIN_RMSE: 5.293333296645416,	VAL_LOSS: 42.67178583705789,	VAL_RMSE: 6.532364490523924


Initial patience 167
2021-01-13 11:10:41.901523 Epoch 14, Training loss 5.366842249153781e-05


[2021-01-13 11:10:52,045] INFO:model_trees_algebra:==> Epoch 14,	TRAIN_LOSS: 27.465081269769026	_TRAIN_RMSE: 5.240713813000003,	VAL_LOSS: 45.76701834096832,	VAL_RMSE: 6.765132544227668
[2021-01-13 11:10:52,045] INFO:model_trees_algebra:==> Epoch 14,	TRAIN_LOSS: 27.465081269769026	_TRAIN_RMSE: 5.240713813000003,	VAL_LOSS: 45.76701834096832,	VAL_RMSE: 6.765132544227668
[2021-01-13 11:10:52,045] INFO:model_trees_algebra:==> Epoch 14,	TRAIN_LOSS: 27.465081269769026	_TRAIN_RMSE: 5.240713813000003,	VAL_LOSS: 45.76701834096832,	VAL_RMSE: 6.765132544227668
[2021-01-13 11:10:52,045] INFO:model_trees_algebra:==> Epoch 14,	TRAIN_LOSS: 27.465081269769026	_TRAIN_RMSE: 5.240713813000003,	VAL_LOSS: 45.76701834096832,	VAL_RMSE: 6.765132544227668
[2021-01-13 11:10:52,045] INFO:model_trees_algebra:==> Epoch 14,	TRAIN_LOSS: 27.465081269769026	_TRAIN_RMSE: 5.240713813000003,	VAL_LOSS: 45.76701834096832,	VAL_RMSE: 6.765132544227668


Initial patience 166


### P1(Baseline Dense Model)

In [8]:
from torch.utils.data import DataLoader
def run_baseline(x_train, y_train, x_val, y_val, maxcardinality, preds2index):
    
    verbose=True
    reg = DenseRegression(
        verbose=True,
         epochs=300,
         query_input_size= len(x_train[0]),
         query_hidden_inputs=[260, 380, 240],
         query_output=1,
#          loss={'func':'CustomMSELoss', 'threshold': 20, 'weight_factor': 1},
         early_stop_patience=10,
         early_stop_initial_patience=80,
         activation_dense=nn.ReLU,
        optimizer={'optimizer': "Adam",'args':{"lr":0.00015}},
        figimage_size=(18,18),
        preds2index=preds2index
    )
    reg.fit(x_train, y_train, x_val, y_val)
    
    pairs_val = list(zip(x_val, y_val))
    dataset_val = DataLoader(pairs_val, batch_size=64, num_workers=0, shuffle=False, collate_fn=reg.collate)
    preds = reg.predict_best(dataset_val)
    y_pred_val, y_real_val = zip(*preds)
    mseval = mean_squared_error(y_real_val, y_pred_val)
    maeval = mean_absolute_error(y_real_val, y_pred_val)
    rmseval = np.sqrt(mseval)
    print("RMSE for baseline: in fold:{}, set VAL: {}".format(fold, rmseval))
#     reg.scatter_image(preds, y_val, "Scatter real latency vs prediction on Val dataset.", "neo_with_aec_scatter_test", max_refference=70, figsize =(15,15))
    return preds , mseval, rmseval, maeval , reg.history

In [ ]:

import pickle
from model_dense import DenseRegression

folds_executiondense = {}
for fold, data in enumerate(datasets_splits):
    
    ds_train = data['train']
    ds_val = data['val']
    
    list_columns = ['assign', 'bgp', 'distinct', 'extend', 'filter', 'graph', 'group',
    'join', 'leftjoin','minus', 'multi', 'notoneof', 'order', 'path*',  'project', 'reduced',
    'sequence', 'slice', 'tolist', 'top','treesize', 'triple', 'union' ,
    'path+', 'path?', 'pathN*', 'pathN+', 'pcs0', 'pcs1', 'pcs2', 'pcs3', 'pcs4',
    'pcs5', 'pcs6', 'pcs7', 'pcs8', 'pcs9', 'pcs10', 'pcs11','pcs12', 'pcs13',
    'pcs14', 'pcs15', 'pcs16', 'pcs17', 'pcs18', 'pcs19', 'pcs20', 'pcs21', 'pcs22', 'pcs23', 'pcs24',
                    'filter_bound', 'filter_contains', 'filter_eq', 'filter_exists',
           'filter_ge', 'filter_gt', 'filter_isBlank', 'filter_isIRI',
           'filter_isLiteral', 'filter_lang', 'filter_langMatches', 'filter_le',
           'filter_lt', 'filter_ne', 'filter_not', 'filter_notexists', 'filter_or',
           'filter_regex', 'filter_sameTerm', 'filter_str', 'filter_strends',
           'filter_strstarts', 'filter_subtract', 'has_slice', 'max_slice_limit', 'max_slice_start','json_cardinality']

    x_train_query = ds_train[list_columns]
    x_val_query   = ds_val[list_columns]

    y_train = ds_train['time'].values
    y_val = ds_val['time'].values

    import json
    def getmax(x):
        lista=  list(x.values())
        maximo = 0
        for el in lista:
            if (maximo < float(el)):
                maximo = float(el)
        return maximo

    def getpreds(values, preds_dic):
        index = len(preds_dic)
        for x in values:
            lista=  list(json.loads(x).keys())
            for el in lista:
                if not el.startswith("http"):
                    continue
                if el not in preds_dic:
                    preds_dic[el] = index
                    index +=1
        return preds_dic

    #Scale x_query data.
    xqtrain = x_train_query.drop(columns=['json_cardinality'])
    xqval   = x_val_query.drop(columns=['json_cardinality'])

    scalerx = StandardScaler()
    x_train_scaled = scalerx.fit_transform(xqtrain)
    x_val_scaled = scalerx.transform(xqval)

    x_train_query =pd.concat([pd.DataFrame(x_train_scaled, index=xqtrain.index, columns=xqtrain.columns),x_train_query[['json_cardinality']]], axis=1)
    x_val_query =  pd.concat([pd.DataFrame(x_val_scaled,   index=xqval.index, columns=xqval.columns),x_val_query[['json_cardinality']]], axis=1)

    preds_dic = {}
    preds_dic = getpreds(x_train_query['json_cardinality'], preds_dic)
    preds_dic = getpreds(x_val_query['json_cardinality'], preds_dic)

    maxcardinality =  x_train_query['json_cardinality'].apply(lambda x: json.loads(x)).apply(lambda x: getmax(x)).max()

    def pred2index_dict(x, pred_to_index):
        resp = {}
        x = json.loads(x)
        for el in x.keys():
            if el in pred_to_index:
                resp[pred_to_index[el]] = float(x[el])/maxcardinality
        return resp

    x_train_query['json_cardinality'] = x_train_query['json_cardinality'].apply(lambda x: pred2index_dict(x, preds_dic))
    x_val_query['json_cardinality'] = x_val_query['json_cardinality'].apply(lambda x: pred2index_dict(x, preds_dic))
    y_train = ds_train['time'].values
    y_val = ds_val['time'].values
    preds , mseval, rmseval, maeval , history = run_baseline(x_train_query.values, y_train, x_val_query.values, y_val, maxcardinality,  preds_dic)
    y_pred_val, y_real_val = zip(*preds)
    folds_executiondense[fold] = {"pred": y_pred_val, "real" : y_real_val, "mse": mseval, "mae": maeval, "rmse": rmseval, "history": history}
    
    file_to_store = open("./folds_execution_baseline.pickle", "wb")
    pickle.dump(folds_executiondense, file_to_store)
    file_to_store.close()
    print("Fold {} baseline Saved!!".format(fold))
#     run_baseline(x_train_query, y_train, x_val_query, y_val)
#     folds_execution[fold] = {"tree_model": getpreds(x_val_tree, x_val_query, y_val)}

Model optimizer: Adam lr: 0.00015
Initial input channels of query model: 79
[Linear(in_features=1770, out_features=260, bias=True), ReLU(), Dropout(p=0.25, inplace=False), Linear(in_features=260, out_features=380, bias=True), ReLU(), Dropout(p=0.25, inplace=False), Linear(in_features=380, out_features=240, bias=True), ReLU(), Dropout(p=0.25, inplace=False), Linear(in_features=240, out_features=1, bias=True)]
Epochs to run: 4
2021-01-13 17:58:45.096713 Epoch 0, Training loss 0.0030035390732673904


### Model with Autoencoder for Tree Nodes, Algebra + Graph Pattern + Filters + Cardinality

In [8]:
file_to_store = open("./select_query_features3.pickle", "wb")
pickle.dump(select_query_features, file_to_store)
file_to_store.close()

### P2

In [ ]:
list_columns = ['assign', 'bgp', 'distinct', 'extend', 'filter', 'graph', 'group',
'join', 'leftjoin','minus', 'multi', 'notoneof', 'order', 'path*',  'project', 'reduced',
'sequence', 'slice', 'tolist', 'top','treesize', 'triple', 'union' ,
'path+', 'path?', 'pathN*', 'pathN+', 'pcs0', 'pcs1', 'pcs2', 'pcs3', 'pcs4',
'pcs5', 'pcs6', 'pcs7', 'pcs8', 'pcs9', 'pcs10', 'pcs11','pcs12', 'pcs13',
'pcs14', 'pcs15', 'pcs16', 'pcs17', 'pcs18', 'pcs19', 'pcs20', 'pcs21', 'pcs22', 'pcs23', 'pcs24',
                'filter_bound', 'filter_contains', 'filter_eq', 'filter_exists',
       'filter_ge', 'filter_gt', 'filter_isBlank', 'filter_isIRI',
       'filter_isLiteral', 'filter_lang', 'filter_langMatches', 'filter_le',
       'filter_lt', 'filter_ne', 'filter_not', 'filter_notexists', 'filter_or',
       'filter_regex', 'filter_sameTerm', 'filter_str', 'filter_strends',
       'filter_strstarts', 'filter_subtract', 'has_slice', 'max_slice_limit', 'max_slice_start','json_cardinality']
import pickle
folds_execution = {}

for fold, data in enumerate(datasets_splits):
    
    # Switch train -> val and val -> train For P2 of Hypotesis Test
    ds_train = data['val']
    ds_val = data['train']
    
    print("Size Train: {}, Val {}, Fold".format(ds_train.shape[0], ds_val.shape[0]), fold)
    
    x_train_query = ds_train[list_columns]
    x_val_query   = ds_val[list_columns]

    x_train_tree = ds_train['trees'].values
    x_val_tree = ds_val['trees'].values

    y_train = ds_train['time'].values
    y_val = ds_val['time'].values



    x_train_tree = ds_train['trees'].values
    x_val_tree = ds_val['trees'].values

    y_train = ds_train['time'].values
    y_val = ds_val['time'].values

    aec_dir = '/workspace/bao_server/aec_wikidata_neo.pth'
    maxcardinality =  x_train_query['json_cardinality'].apply(lambda x: json.loads(x)).apply(lambda x: getmax(x)).max()

    verbose=True
    reg = NeoRegression(
         aec={'train_aec': False, 'use_aec': True,'aec_file': aec_dir+str(fold)+'.pth', 'aec_epochs': 200},
         epochs=300,
         maxcardinality=maxcardinality,
         in_channels_neo_net=512,
         tree_units=[512, 256, 128],
         tree_units_dense=[64, 32],
         early_stop_patience=10,
         early_stop_initial_patience=180,
         tree_activation_tree=nn.LeakyReLU,
         tree_activation_dense=nn.ReLU,
        optimizer={'optimizer': "Adam",'args':{"lr":0.00015}},
        figimage_size=(18,18),
        start_history_from_epoch=3
    )

    #Fit the transformer tree data
    reg.fit_transform_tree_data(ds_train, ds_val, ds_val)
    print("Trees tranformed!!!")

    x_train_query, x_val_query =  prepare_query_level_data(x_train_query, x_val_query)

    #Fit model
    reg.fit(x_train_tree, x_train_query.values, y_train, x_val_tree, x_val_query.values, y_val)
    folds_execution[fold] = {"tree_model": getpredictions_info(x_val_tree, x_val_query, y_val)}

    file_to_store = open("./folds_execution_p2.pickle", "wb")
    pickle.dump(folds_execution, file_to_store)
    file_to_store.close()
#     run_baseline(x_train_query, y_train, x_val_query, y_val)
#     folds_execution[fold] = {"tree_model": getpreds(x_val_tree, x_val_query, y_val)}

Size Train: 10849, Val 10848, Fold 0
Model optimizer: Adam lr: 0.00015
Trees tranformed!!!
X_train loaded
X_val loaded
Transforming Trees
Activation function in treeConv layers: <class 'torch.nn.modules.activation.LeakyReLU'>
Activation function in tree dense output layers: <class 'torch.nn.modules.activation.ReLU'>
[BinaryTreeConvWithQData(
  (weights): Conv1d(2086, 512, kernel_size=(3,), stride=(3,))
), TreeLayerNorm(), TreeActivation(
  (activation): LeakyReLU(negative_slope=0.01)
), BinaryTreeConv(
  (weights): Conv1d(512, 256, kernel_size=(3,), stride=(3,))
), TreeLayerNorm(), TreeActivation(
  (activation): LeakyReLU(negative_slope=0.01)
), BinaryTreeConv(
  (weights): Conv1d(256, 128, kernel_size=(3,), stride=(3,))
), TreeLayerNorm(), TreeActivation(
  (activation): LeakyReLU(negative_slope=0.01)
), DynamicPooling(), Linear(in_features=128, out_features=64, bias=True), ReLU(), Linear(in_features=64, out_features=32, bias=True), ReLU(), Linear(in_features=32, out_features=1, bias

[2021-01-13 23:16:44,859] INFO:model_trees_algebra:==> Epoch 0,	TRAIN_LOSS: 3108.80747368557	_TRAIN_RMSE: 55.75668097802783,	VAL_LOSS: 672.8763355411992,	VAL_RMSE: 25.93985997535837


Initial patience 180
2021-01-13 23:16:57.498354 Epoch 1, Training loss 0.00017907107103886695


[2021-01-13 23:17:06,966] INFO:model_trees_algebra:==> Epoch 1,	TRAIN_LOSS: 1661.2365551386463	_TRAIN_RMSE: 40.758269776066875,	VAL_LOSS: 2884.4677826579536,	VAL_RMSE: 53.707241435936304


Initial patience 179
2021-01-13 23:17:25.047506 Epoch 2, Training loss 0.00011118449681602857


...

Initial patience 97
2021-01-13 23:55:13.924898 Epoch 84, Training loss 3.670131767315268e-05


[2021-01-13 23:55:23,407] INFO:model_trees_algebra:==> Epoch 84,	TRAIN_LOSS: 18.503203210695293	_TRAIN_RMSE: 4.30153498308398,	VAL_LOSS: 34.78182480762561,	VAL_RMSE: 5.8976117884806225


Initial patience 96
2021-01-13 23:55:41.559182 Epoch 85, Training loss 3.633829468142589e-05


[2021-01-13 23:55:50,982] INFO:model_trees_algebra:==> Epoch 85,	TRAIN_LOSS: 17.416429809839688	_TRAIN_RMSE: 4.173299630968245,	VAL_LOSS: 34.48460445084555,	VAL_RMSE: 5.872359359818296


Initial patience 95


### P2 Baseline

In [ ]:

import pickle
from model_dense import DenseRegression

folds_executiondense = {}
for fold, data in enumerate(datasets_splits):
    
    # Switch train -> val and val -> train For P2 of Hypotesis Test
    ds_train = data['val']
    ds_val = data['train']
    
    list_columns = ['assign', 'bgp', 'distinct', 'extend', 'filter', 'graph', 'group',
    'join', 'leftjoin','minus', 'multi', 'notoneof', 'order', 'path*',  'project', 'reduced',
    'sequence', 'slice', 'tolist', 'top','treesize', 'triple', 'union' ,
    'path+', 'path?', 'pathN*', 'pathN+', 'pcs0', 'pcs1', 'pcs2', 'pcs3', 'pcs4',
    'pcs5', 'pcs6', 'pcs7', 'pcs8', 'pcs9', 'pcs10', 'pcs11','pcs12', 'pcs13',
    'pcs14', 'pcs15', 'pcs16', 'pcs17', 'pcs18', 'pcs19', 'pcs20', 'pcs21', 'pcs22', 'pcs23', 'pcs24',
                    'filter_bound', 'filter_contains', 'filter_eq', 'filter_exists',
           'filter_ge', 'filter_gt', 'filter_isBlank', 'filter_isIRI',
           'filter_isLiteral', 'filter_lang', 'filter_langMatches', 'filter_le',
           'filter_lt', 'filter_ne', 'filter_not', 'filter_notexists', 'filter_or',
           'filter_regex', 'filter_sameTerm', 'filter_str', 'filter_strends',
           'filter_strstarts', 'filter_subtract', 'has_slice', 'max_slice_limit', 'max_slice_start','json_cardinality']

    x_train_query = ds_train[list_columns]
    x_val_query   = ds_val[list_columns]

    y_train = ds_train['time'].values
    y_val = ds_val['time'].values

    import json
    def getmax(x):
        lista=  list(x.values())
        maximo = 0
        for el in lista:
            if (maximo < float(el)):
                maximo = float(el)
        return maximo

    def getpreds(values, preds_dic):
        index = len(preds_dic)
        for x in values:
            lista=  list(json.loads(x).keys())
            for el in lista:
                if not el.startswith("http"):
                    continue
                if el not in preds_dic:
                    preds_dic[el] = index
                    index +=1
        return preds_dic

    #Scale x_query data.
    xqtrain = x_train_query.drop(columns=['json_cardinality'])
    xqval   = x_val_query.drop(columns=['json_cardinality'])

    scalerx = StandardScaler()
    x_train_scaled = scalerx.fit_transform(xqtrain)
    x_val_scaled = scalerx.transform(xqval)

    x_train_query =pd.concat([pd.DataFrame(x_train_scaled, index=xqtrain.index, columns=xqtrain.columns),x_train_query[['json_cardinality']]], axis=1)
    x_val_query =  pd.concat([pd.DataFrame(x_val_scaled,   index=xqval.index, columns=xqval.columns),x_val_query[['json_cardinality']]], axis=1)

    preds_dic = {}
    preds_dic = getpreds(x_train_query['json_cardinality'], preds_dic)
    preds_dic = getpreds(x_val_query['json_cardinality'], preds_dic)

    maxcardinality =  x_train_query['json_cardinality'].apply(lambda x: json.loads(x)).apply(lambda x: getmax(x)).max()

    def pred2index_dict(x, pred_to_index):
        resp = {}
        x = json.loads(x)
        for el in x.keys():
            if el in pred_to_index:
                resp[pred_to_index[el]] = float(x[el])/maxcardinality
        return resp

    x_train_query['json_cardinality'] = x_train_query['json_cardinality'].apply(lambda x: pred2index_dict(x, preds_dic))
    x_val_query['json_cardinality'] = x_val_query['json_cardinality'].apply(lambda x: pred2index_dict(x, preds_dic))
    y_train = ds_train['time'].values
    y_val = ds_val['time'].values
    preds , mseval, rmseval, maeval , history = run_baseline(x_train_query.values, y_train, x_val_query.values, y_val, maxcardinality,  preds_dic)
    y_pred_val, y_real_val = zip(*preds)
    folds_executiondense[fold] = {"pred": y_pred_val, "real" : y_real_val, "mse": mseval, "mae": maeval, "rmse": rmseval, "history": history}
    
    file_to_store = open("./folds_execution_baseline_p2.pickle", "wb")
    pickle.dump(folds_executiondense, file_to_store)
    file_to_store.close()
    print("Fold {} baseline Saved!!".format(fold))
#     run_baseline(x_train_query, y_train, x_val_query, y_val)
#     folds_execution[fold] = {"tree_model": getpreds(x_val_tree, x_val_query, y_val)}

Model optimizer: Adam lr: 0.00015
Initial input channels of query model: 79
[Linear(in_features=1770, out_features=260, bias=True), ReLU(), Dropout(p=0.25, inplace=False), Linear(in_features=260, out_features=380, bias=True), ReLU(), Dropout(p=0.25, inplace=False), Linear(in_features=380, out_features=240, bias=True), ReLU(), Dropout(p=0.25, inplace=False), Linear(in_features=240, out_features=1, bias=True)]
Epochs to run: 4
2021-01-14 12:25:40.116161 Epoch 0, Training loss 0.002586816598219508


[2021-01-14 12:25:43,310] INFO:model_dense:==> Epoch 0, 	TRAIN_LOSS: 441.1220397949219	_TRAIN_RMSE: 21.002904891967773, 	VAL_LOSS: 15460231.0, 	VAL_RMSE: 3931.949951171875
[2021-01-14 12:25:43,310] INFO:model_dense:==> Epoch 0, 	TRAIN_LOSS: 441.1220397949219	_TRAIN_RMSE: 21.002904891967773, 	VAL_LOSS: 15460231.0, 	VAL_RMSE: 3931.949951171875
[2021-01-14 12:25:43,310] INFO:model_dense:==> Epoch 0, 	TRAIN_LOSS: 441.1220397949219	_TRAIN_RMSE: 21.002904891967773, 	VAL_LOSS: 15460231.0, 	VAL_RMSE: 3931.949951171875
[2021-01-14 12:25:43,310] INFO:model_dense:==> Epoch 0, 	TRAIN_LOSS: 441.1220397949219	_TRAIN_RMSE: 21.002904891967773, 	VAL_LOSS: 15460231.0, 	VAL_RMSE: 3931.949951171875
[2021-01-14 12:25:43,310] INFO:model_dense:==> Epoch 0, 	TRAIN_LOSS: 441.1220397949219	_TRAIN_RMSE: 21.002904891967773, 	VAL_LOSS: 15460231.0, 	VAL_RMSE: 3931.949951171875
[2021-01-14 12:25:43,310] INFO:model_dense:==> Epoch 0, 	TRAIN_LOSS: 441.1220397949219	_TRAIN_RMSE: 21.002904891967773, 	VAL_LOSS: 15460231.

Initial patience 180
2021-01-14 12:25:46.905397 Epoch 1, Training loss 0.001027896593331388


[2021-01-14 12:25:50,126] INFO:model_dense:==> Epoch 1, 	TRAIN_LOSS: 2191.197509765625	_TRAIN_RMSE: 46.81023025512695, 	VAL_LOSS: 223.7170867919922, 	VAL_RMSE: 14.957175254821777
[2021-01-14 12:25:50,126] INFO:model_dense:==> Epoch 1, 	TRAIN_LOSS: 2191.197509765625	_TRAIN_RMSE: 46.81023025512695, 	VAL_LOSS: 223.7170867919922, 	VAL_RMSE: 14.957175254821777
[2021-01-14 12:25:50,126] INFO:model_dense:==> Epoch 1, 	TRAIN_LOSS: 2191.197509765625	_TRAIN_RMSE: 46.81023025512695, 	VAL_LOSS: 223.7170867919922, 	VAL_RMSE: 14.957175254821777
[2021-01-14 12:25:50,126] INFO:model_dense:==> Epoch 1, 	TRAIN_LOSS: 2191.197509765625	_TRAIN_RMSE: 46.81023025512695, 	VAL_LOSS: 223.7170867919922, 	VAL_RMSE: 14.957175254821777
[2021-01-14 12:25:50,126] INFO:model_dense:==> Epoch 1, 	TRAIN_LOSS: 2191.197509765625	_TRAIN_RMSE: 46.81023025512695, 	VAL_LOSS: 223.7170867919922, 	VAL_RMSE: 14.957175254821777
[2021-01-14 12:25:50,126] INFO:model_dense:==> Epoch 1, 	TRAIN_LOSS: 2191.197509765625	_TRAIN_RMSE: 46.81

Initial patience 179
2021-01-14 12:25:59.236308 Epoch 2, Training loss 0.0009044514673829014


...

Initial patience 35
2021-01-14 16:57:53.123173 Epoch 146, Training loss 0.0004773185759170304


[2021-01-14 16:57:56,075] INFO:model_dense:==> Epoch 146, 	TRAIN_LOSS: 113.0798110961914	_TRAIN_RMSE: 10.633898735046387, 	VAL_LOSS: 118.02198791503906, 	VAL_RMSE: 10.863792419433594
[2021-01-14 16:57:56,075] INFO:model_dense:==> Epoch 146, 	TRAIN_LOSS: 113.0798110961914	_TRAIN_RMSE: 10.633898735046387, 	VAL_LOSS: 118.02198791503906, 	VAL_RMSE: 10.863792419433594
[2021-01-14 16:57:56,075] INFO:model_dense:==> Epoch 146, 	TRAIN_LOSS: 113.0798110961914	_TRAIN_RMSE: 10.633898735046387, 	VAL_LOSS: 118.02198791503906, 	VAL_RMSE: 10.863792419433594
[2021-01-14 16:57:56,075] INFO:model_dense:==> Epoch 146, 	TRAIN_LOSS: 113.0798110961914	_TRAIN_RMSE: 10.633898735046387, 	VAL_LOSS: 118.02198791503906, 	VAL_RMSE: 10.863792419433594
[2021-01-14 16:57:56,075] INFO:model_dense:==> Epoch 146, 	TRAIN_LOSS: 113.0798110961914	_TRAIN_RMSE: 10.633898735046387, 	VAL_LOSS: 118.02198791503906, 	VAL_RMSE: 10.863792419433594
[2021-01-14 16:57:56,075] INFO:model_dense:==> Epoch 146, 	TRAIN_LOSS: 113.0798110961

Initial patience 34
2021-01-14 16:58:05.223828 Epoch 147, Training loss 0.0004731766147193488


[2021-01-14 16:58:08,160] INFO:model_dense:==> Epoch 147, 	TRAIN_LOSS: 174.15614318847656	_TRAIN_RMSE: 13.196823120117188, 	VAL_LOSS: 118.77289581298828, 	VAL_RMSE: 10.898298263549805
[2021-01-14 16:58:08,160] INFO:model_dense:==> Epoch 147, 	TRAIN_LOSS: 174.15614318847656	_TRAIN_RMSE: 13.196823120117188, 	VAL_LOSS: 118.77289581298828, 	VAL_RMSE: 10.898298263549805
[2021-01-14 16:58:08,160] INFO:model_dense:==> Epoch 147, 	TRAIN_LOSS: 174.15614318847656	_TRAIN_RMSE: 13.196823120117188, 	VAL_LOSS: 118.77289581298828, 	VAL_RMSE: 10.898298263549805
[2021-01-14 16:58:08,160] INFO:model_dense:==> Epoch 147, 	TRAIN_LOSS: 174.15614318847656	_TRAIN_RMSE: 13.196823120117188, 	VAL_LOSS: 118.77289581298828, 	VAL_RMSE: 10.898298263549805
[2021-01-14 16:58:08,160] INFO:model_dense:==> Epoch 147, 	TRAIN_LOSS: 174.15614318847656	_TRAIN_RMSE: 13.196823120117188, 	VAL_LOSS: 118.77289581298828, 	VAL_RMSE: 10.898298263549805
[2021-01-14 16:58:08,160] INFO:model_dense:==> Epoch 147, 	TRAIN_LOSS: 174.15614

Initial patience 33


### Test de Hipótesis 5x2cv paired  *t*

- Split dataset in 50/50 train and val.

- Run 5 times, where $p^{(1)}$ is fit over $train$ and evaluated over $val$

  $p^{(1)} = p^{(1)}_A - p^{(1)}_B$

- Switch train and val and run 5 times, where $p^{(2)}$ is fit over $val$ and evaluated over $train$

  $p^{(2)} = p^{(2)}_A - p^{(2)}_B$

- Then, we estimate the estimate mean and variance of the differences:

  $\overline{p} = \frac{p^{(1)} + p^{(2)}}{2}$

  $s^2 = (p^{(1)} - \overline{p})^2 + (p^{(2)} - \overline{p})^2.$

- The variance of the difference is computed for the 5 iterations and then used to compute the t statistic as follows:

  $t = \frac{p_1^{(1)}}{\sqrt{(1/5) \sum_{i=1}^{5}s_i^2}}$

In [48]:
# Load data

data_p1_A = pickle.load(open("./folds_execution.pickle", "rb"))
data_p2_A = pickle.load(open("./folds_execution_p2.pickle", "rb"))

data_p1_B = pickle.load(open("./folds_execution_baseline.pickle", "rb"))
data_p2_B = pickle.load(open("./folds_execution_baseline_p2.pickle", "rb"))


In [37]:
data_p2_A[1]['tree_model']['rmse']

6.410662815326585

In [52]:
from scipy import stats
p_mean_list = []
p_variance_list = []
p1_list = []
p2_list = []

for i in range(5):
    p1_a = data_p1_A[i]['tree_model']['rmse']
    p1_b = data_p1_B[i]['rmse']
    p1 = p1_a - p1_b
    
    p2_a = data_p2_A[i]['tree_model']['rmse']
    p2_b = data_p2_B[i]['rmse']
    p2 = p2_a - p2_b
    
    p_mean = (p1 + p2)/2.
    p_variance = ((p1 - p_mean)**2 + (p2 - p_mean)**2)
    p1_list.append(p1)
    p2_list.append(p2)
    p_mean_list.append(p_mean)
    p_variance_list.append(p_variance)

t_stat = (p1_list[0])/np.sqrt(np.mean(p_variance_list))
pvalue = stats.t.sf(np.abs(t_stat), 5)*2.

print(f"T: {t_stat} , p-value: {pvalue}")
if pvalue <= 0.05:
    print('Since p<0.05, We can reject the null-hypothesis that both models perform equally well on this dataset. We may conclude that the two algorithms are significantly different.')
else:
    print('Since p>0.05, we cannot reject the null hypothesis and may conclude that the performance of the two algorithms is not significantly different.')

T: -32.518218285396365 , p-value: 5.167491541893221e-07
Since p<0.05, We can reject the null-hypothesis that both models perform equally well on this dataset. We may conclude that the two algorithms are significantly different.


In [55]:
data_p1_A.keys()

dict_keys([0, 1, 2, 3, 4])

sepal_length  sepal_width  petal_length  petal_width    species  \
0             5.1          3.5           1.4          0.2     setosa   
1             4.9          3.0           1.4          0.2     setosa   
2             4.7          3.2           1.3          0.2     setosa   
3             4.6          3.1           1.5          0.2     setosa   
4             5.0          3.6           1.4          0.2     setosa   
5             5.4          3.9           1.7          0.4     setosa   
6             4.6          3.4           1.4          0.3     setosa   
7             5.0          3.4           1.5          0.2     setosa   
8             4.4          2.9           1.4          0.2     setosa   
9             4.9          3.1           1.5          0.1     setosa   
10            5.4          3.7           1.5          0.2     setosa   
11            4.8          3.4           1.6          0.2     setosa   
12            4.8          3.0           1.4          0.1     setosa   
13            4.3          3.0           1.1          0.1     setosa   
14            5.8          4.0           1.2          0.2     setosa   
15            5.7          4.4           1.5          0.4     setosa   
16            5.4          3.9           1.3          0.4     setosa   
17            5.1          3.5           1.4          0.3     setosa   
18            5.7          3.8           1.7          0.3     setosa   
19            5.1          3.8           1.5          0.3     setosa   
20            5.4          3.4           1.7          0.2     setosa   
21            5.1          3.7           1.5          0.4     setosa   
22            4.6          3.6           1.0          0.2     setosa   
23            5.1          3.3           1.7          0.5     setosa   
24            4.8          3.4           1.9          0.2     setosa   
25            5.0          3.0           1.6          0.2     setosa   
26            5.0          3.4           1.6          0.4     setosa   
27            5.2          3.5           1.5          0.2     setosa   
28            5.2          3.4           1.4          0.2     setosa   
29            4.7          3.2           1.6          0.2     setosa   
..            ...          ...           ...          ...        ...   
120           6.9          3.2           5.7          2.3  virginica   
121           5.6          2.8           4.9          2.0  virginica   
122           7.7          2.8           6.7          2.0  virginica   
123           6.3          2.7           4.9          1.8  virginica   
124           6.7          3.3           5.7          2.1  virginica   
125           7.2          3.2           6.0          1.8  virginica   
126           6.2          2.8           4.8          1.8  virginica   
127           6.1          3.0           4.9          1.8  virginica   
128           6.4          2.8           5.6          2.1  virginica   
129           7.2          3.0           5.8          1.6  virginica   
130           7.4          2.8           6.1          1.9  virginica   
131           7.9          3.8           6.4          2.0  virginica   
132           6.4          2.8           5.6          2.2  virginica   
133           6.3          2.8           5.1          1.5  virginica   
134           6.1          2.6           5.6          1.4  virginica   
135           7.7          3.0           6.1          2.3  virginica   
136           6.3          3.4           5.6          2.4  virginica   
137           6.4          3.1           5.5          1.8  virginica   
138           6.0          3.0           4.8          1.8  virginica   
139           6.9          3.1           5.4          2.1  virginica   
140           6.7          3.1           5.6          2.4  virginica   
141           6.9          3.1           5.1          2.3  virginica   
142           5.8          2.7           5.1          1.9  virginica   
143           6.8          3.2           5.9 